---
title: "LSE DS202W 2025: Week 4 - Student Notebook"
subtitle: "2024/25 Winter Term"
author: "The DS202 Team"
date: 10 February 2025
---

# ⚙️ Setup

**Import required libraries:**

In [10]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import Lasso
from sklearn.metrics import precision_score, recall_score, f1_score, root_mean_squared_error
import statsmodels.api as sm
from lets_plot import *
LetsPlot.setup_html()

## Before we do anything more

Please create a data folder called `data` to store all the different data sets in this course if you haven't already done so.

# 📋 Lab Tasks

## Part I - Cleaning a new data set `monitor` (30 min)

The first step is to load the dataset. In this lab, we will be using the 2020 Wellcome Trust Global Monitor (`monitor`) dataset which contains data. It includes variables associated with trust in various actors and demographic information:

-   `science_decreases_jobs`: binary outcome where respondents are asked whether they believe science and technology will decrease (versus increase, or have no impact on) the amount of jobs available. 
-   `trust_neighbours`: Trust People in Neighbourhood
-   `trust_government`: Trust the National Government in This Country
-   `trust_scientists`: Trust Scientists in This Country
-   `trust_journalists`: Trust Journalists in This Country
-   `trust_doctors`: Trust Doctors and Nurses in This Country
-   `trust_ngos`: Trust People Who Work at Charitable Organizations or NGOs in This Country
-   `trust_trad_healers`: Trust Traditional Healers in This Country
-   `age`: Age (years)
-   `gender`: Male / Female
-   `education`: Education Level (Elementary / Secondary / Tertiary)
-   `hh_income`: Per Capita Income Quintiles
-   `subj_income`: Feelings About Household Income
-   `emp_status`: Employment Status

👉 **NOTE:** With variables such as `trust_neighbours`, we recoded the original question to a trust / no trust binary mainly for the sake of simplicity. This simplification can be useful as it reduces the number of parameters in our model. However, there may be distinct differences between each level that may produce different results.

In [11]:
monitor = pd.read_csv("data/wellcome_global_monitor.csv")

📝**Task:** Check the dimensions of the dataframe.

In [4]:
# Code here

(119088, 14)


📝**Task:** Here's another check we can perform quickly in `pandas`.  If we use the `isnull` method and then calculate the mean, we can check the proportion of missing values contained within each variable.

In [7]:
# Code here

📝**Task:** We need to perform some variable transformations. Normalise `age`, convert all logical variables to integer variables (check out `astype`), and code all categorical features as one-hot encoded dummies.

In [6]:
# Code here

📝**Task:** How many observations fall into each class of the variable `science_decreases_jobs`? Comment. What are the challenges you would expect when training a model?

In [2]:
# Code here

📝**Task:** Come up with one or two summary visualisations using either `monitor` or `monitor_cleaned`!

In [1]:
# Code here

## Part II - Fitting a logistic regression (40 min)

We want to perform a logistic regression using the available variables in the dataset to predict whether an individual thinks that science will decrease jobs.

👨🏻‍🏫 **TEACHING MOMENT:** Your class teacher will formalize the logistic regression in the context of the data at our disposal.

Now, we need to split the data into training and testing sets. Having a test set will help us evaluate how well the model performs.

-   In the training phase, we will use part of the data to fit the logistic regression model.
-   In the testing phase, we will assess the model's performance on the remaining data (test set) which was not used during training.

In [40]:
# Divide data into features (X) and targets (y) 
X = monitor_cleaned.drop("science_decreases_jobs", axis=1).astype(float)
X = sm.add_constant(X)
y = monitor_cleaned["science_decreases_jobs"].astype(int)

# Perform a 0.75 / 0.25 train / test
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=123)

💡**Tip:** When using `train_test_split` try specifying `stratify = y`. This ensures that the training and test sets will have identical proportions of the outcome.

We will now fit a logistic regression model on the training data using `statsmodels`.

In [41]:
logit_model = sm.Logit(y_train, X_train).fit()
print(logit_model.summary())

Optimization terminated successfully.
         Current function value: 0.595142
         Iterations 5
                             Logit Regression Results                             
Dep. Variable:     science_decreases_jobs   No. Observations:                89316
Model:                              Logit   Df Residuals:                    89292
Method:                               MLE   Df Model:                           23
Date:                    Thu, 06 Feb 2025   Pseudo R-squ.:                 0.02893
Time:                            09:32:51   Log-Likelihood:                -53156.
converged:                           True   LL-Null:                       -54739.
Covariance Type:                nonrobust   LLR p-value:                     0.000
                                                              coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------------------------------------------------------------------

👨🏻‍🏫 **TEACHING MOMENT:** Your class teacher will explain how to interpret the summary of the model ($p-$values, AIC ...).

We can run the same model using `scikit-learn` by specifying the following code.

In [42]:
# Instantiate / fit a logistic regression model
logit_model = LogisticRegression() 
logit_model.fit(X_train, y_train)

LogisticRegression()

Next, we will generate predicted probabilities on both the training and testing sets from our logistic regression model using `predict_proba`.

In [43]:
# Generate predictions on the training set
train_probas = logit_model.predict_proba(X_train)[:,1]

# Generate predictions on the testing set
test_probas = logit_model.predict_proba(X_test)[:,1]

💡**Tip:** `predict_proba` produces a 2-d numpy array which predicts the probability of the outcome not occurring (the 1st dimension) and occurring (the 2nd dimension). To select the 2nd dimension (and all the rows), employ this indexing `[:,1]` when using this function.

In [44]:
test_probas[0:10]

array([0.26031154, 0.35727596, 0.46766817, 0.33238068, 0.22080559,
       0.29925601, 0.28789836, 0.42926639, 0.36675032, 0.32610668])

We are going to set an arbitrary threshold $\alpha$. All the scores that are higher than $\alpha=0.6$ will be classified as 1 and the scores lower than $\alpha=0.6$ will be classified as 0.

In [45]:
# Convert predicted scores to binary outcomes for the training set
train_preds = np.where(train_probas > 0.6, 1, 0)

# Convert predicted scores to binary outcomes for the testing set
test_preds = np.where(test_probas > 0.6, 1, 0)

👨🏻‍🏫 **TEACHING MOMENT:** Your class teacher will explain what precision and recall are.

Now, let's print the precision and recall for both training and testing sets.

In [59]:
print(f"Training set precision: {np.round(precision_score(y_train, train_preds), 3)}")
print(f"Testing set precision: {np.round(precision_score(y_test, test_preds), 3)}")
print(f"Training set recall: {np.round(recall_score(y_train, train_preds), 3)}")
print(f"Testing set recall: {np.round(recall_score(y_test, test_preds), 3)}")

Training set precision: 0.477
Testing set precision: 0.467
Training set recall: 0.001
Testing set recall: 0.001


❓**Question:** Compare the results you obtain for both the training and testing sets. Was this expected ? Does the model overfit ? underfit ?

❓**Question:** What is the problem with setting an arbitrary threshold $\alpha=0.6$ ? How should we expect the precision and the recall to behave if we increase the threshold $\alpha$ ? If we decrease $\alpha$ ?

We will now compute the precision and recall for the test set for different values of the threshold $\alpha$. Compute them for $\alpha \in \{0.1, 0.2, 0.3, 0.4, 0.5, 0.6 \}$.

In [17]:
th_list = np.arange(0.1, 0.7, 0.1)

def test_proba_th(th, prob_est, truth):
  class_preds = np.where(prob_est > th, 1, 0)
  prec = precision_score(truth, class_preds)
  sens = recall_score(truth, class_preds)
  return prec, sens

metrics = [test_proba_th(th,train_probas,y_train) for th in th_list]

output = pd.DataFrame({"threshold": th_list, 
                       "Precision": [m[0] for m in metrics],
                       "Recall": [m[1] for m in metrics]})

output

threshold  Precision    Recall
0        0.1   0.302387  1.000000
1        0.2   0.315991  0.949459
2        0.3   0.382039  0.562648
3        0.4   0.440926  0.226340
4        0.5   0.509091  0.034212
5        0.6   0.477273  0.000778

👨🏻‍🏫 **TEACHING MOMENT:** Your teacher will explain what the code chunk is doing.

-   We specify a probability threshold range using `np.arange`. Note, when we specify an interval of 0.1, we need to set the maximum value to 0.7 to get 0.6.
-   We build a function using `np.where` that creates a binary variable depending on the probability threshold selected and then calculates precision / recall scores.
-   We loop the function over the different thresholds using list comprehension.
-   We create a data frame with the thresholds and precision and recall scores. While we have a list of thresholds, we need to use list comprehension to get the correct dimension of `metrics`, which is a 2-d numpy array.

Let's create a plot that shows performance over different thresholds, using colour to distinguish between the different evaluation metrics.

In [18]:
output_melted = pd.melt(output, id_vars="threshold")

(
  ggplot(output_melted, aes("threshold", "value", colour = "variable", linetype = "variable")) +
  geom_line() +
  theme(panel_grid_minor = element_blank(),
        panel_grid_major_x = element_blank(),
        legend_position = "bottom") +
  labs(x = "Probability threshold", y = "Score", colour = "Metric", linetype = "Metric")
)

📝**Task:** Try redefining `class_metrics` to also include `f1_score` and see what happens.

In [3]:
# Code here

📝**Task:** Based on the precision and recall values you calculated, create a precision-recall plot to visualize the relationship between these two metrics. How does the shape of the precision-recall curve help you assess model performance ? What trade-offs do you observe between precision and recall?

In [6]:
# Code here

## Working with time-series cross-sectional data in machine learning (30 mins)

Economists and political scientists constantly work with data that has a cross-sectional (e.g. between country) and time-series (e.g. within countries over years) structure.  This poses an interesting challenge for when we perform a train / test split. If we use `train_test_split` on such data, the function will assume that it is cross-sectional and perform an initial split without taking the time-series dimension into account.  In doing so, we run the risk of:

-   Using future values to predict the past
-   Using information from the same country in the training and testing sets

Naturally, a few solutions follow from this issue:

-   Use earlier years to train the model and later years to test it.
-   Use some countries to train the model and other countries to test it.

📝**Task:** Use GDP per capita in the Gapminder data set (see the Week 2 lab) to predict life expectancy.

Open the data set.

In [209]:
# Code here

Convert the variable names to snake case (see Lab 2).

In [210]:
# Code here

### Splitting the data by year

Use data from 2007 as the testing data, and all other years as the training data.

In [211]:
# Code here

Split the training / testing data into outcomes and features (remember to convert the series into a one-column data frame).

In [212]:
# Code here

Build a linear model on the training set, and evaluate it on the test set, using RMSE

In [214]:
# Code here

On average, our model is approximately 10.05 years off!


### Splitting the data by country

Create an array of all unique country values.

In [215]:
# Code here

Randomly sample 36 countries (~25% of all countries in `gapminder`) to be in the test set.

💁**Tip:** You'll need a couple of functions from `numpy.random` first, to set a random seed (`seed`) for reproduceability and, second, to select the number of countries (`choice`). 

In [216]:
# Code here

Split the data into training and testing sets.

In [217]:
# Code here

Split the training / testing data into outcomes and features (remember to convert the series into a one-column data frame).

In [5]:
# Code here

Build a linear model on the training set, and evaluate it on the test set, using RMSE

In [4]:
# Code here

👉 **NOTE:** When working with TSCS data, you may need to calculate 1 or more period lags for all features to reduce the possibility of reverse causation.  We have not opted to do this in order to focus on the train / test split itself but these should nevertheless be considered in the real world.